## Result Analysis and Visuals

In [90]:
def print_experiment_names(file_path):
    
    experiment_names = []
    
    with open(file_path, 'r') as file:
        for line in file:
            if "Found entry:" in line:
                experiment_name = line.split("Found entry:")[1].strip()
                experiment_names.append(experiment_name)
    
    print(f"Found {len(experiment_names)} experiments in {file_path}:")
    for i, name in enumerate(experiment_names, 1):
        print(f"{i}. {name}")
    
    return experiment_names

file_path = "/home/robin/Research/qtype-eval/scripts/visualization/combined_results/analysis_output/collect_results.txt" 
experiments_txt = print_experiment_names(file_path)
print(f"Total experiments found: {len(experiments_txt)}")

Found 1051 experiments in /home/robin/Research/qtype-eval/scripts/visualization/combined_results/analysis_output/collect_results.txt:
1. dummy_complexity_all
2. dummy_complexity_control1_all
3. dummy_complexity_control2_all
4. dummy_complexity_control3_all
5. tfidf_DummyClassifier_question_type
6. tfidf_DummyClassifier_question_type_control1
7. tfidf_DummyClassifier_question_type_control2
8. tfidf_DummyClassifier_question_type_control3
9. xgboost_question_type_all
10. xgboost_question_type_control1_all
11. xgboost_question_type_control2_all
12. xgboost_question_type_control3_all
13. tfidf_XGBRegressor_complexity_lexical_density
14. tfidf_XGBRegressor_complexity_control1_lexical_density
15. tfidf_XGBRegressor_complexity_control2_lexical_density
16. tfidf_XGBRegressor_complexity_control3_lexical_density
17. tfidf_XGBRegressor_complexity_avg_max_depth
18. tfidf_XGBRegressor_complexity_control1_avg_max_depth
19. tfidf_XGBRegressor_complexity_control2_avg_max_depth
20. tfidf_XGBRegressor_co

In [92]:
import json

def print_experiment_names(file_path):
    experiment_names = []
    
    with open(file_path, 'r') as file:
        data = json.load(file)
        experiment_names = list(data.keys())
    
    print(f"Found {len(experiment_names)} experiments in {file_path}:")
    for i, name in enumerate(experiment_names, 1):
        print(f"{i}. {name}")
    
    return experiment_names

file_path = "/home/robin/Research/qtype-eval/scripts/visualization/combined_results/analysis_output/collect_results.json"
experiments_json = print_experiment_names(file_path)
print(f"Total experiments found: {len(experiments_json)}")

with open('/home/robin/Research/qtype-eval/scripts/visualization/combined_results/analysis_output/experiment_list.txt', "w") as f:
    for experiment in experiments_json:
        f.write(experiment + "\n")

Found 1051 experiments in /home/robin/Research/qtype-eval/scripts/visualization/combined_results/analysis_output/collect_results.json:
1. dummy_complexity_all
2. dummy_complexity_control1_all
3. dummy_complexity_control2_all
4. dummy_complexity_control3_all
5. tfidf_DummyClassifier_question_type
6. tfidf_DummyClassifier_question_type_control1
7. tfidf_DummyClassifier_question_type_control2
8. tfidf_DummyClassifier_question_type_control3
9. xgboost_question_type_all
10. xgboost_question_type_control1_all
11. xgboost_question_type_control2_all
12. xgboost_question_type_control3_all
13. tfidf_XGBRegressor_complexity_lexical_density
14. tfidf_XGBRegressor_complexity_control1_lexical_density
15. tfidf_XGBRegressor_complexity_control2_lexical_density
16. tfidf_XGBRegressor_complexity_control3_lexical_density
17. tfidf_XGBRegressor_complexity_avg_max_depth
18. tfidf_XGBRegressor_complexity_control1_avg_max_depth
19. tfidf_XGBRegressor_complexity_control2_avg_max_depth
20. tfidf_XGBRegressor_c

In [ ]:
import json
import pandas as pd
import re
from collections import defaultdict
from IPython.display import display, HTML

with open("/home/robin/Research/qtype-eval/scripts/visualization/combined_results/analysis_output/collect_results.json", "r") as f:
    results = json.load(f)

def extract_layer(model_key):
    match = re.search(r"layer(\d+)", model_key)
    return int(match.group(1)) if match else None

rows = []
control_accumulator = defaultdict(list)

for model_key, res in results.items():
    model_type = res.get("model_type")
    task = res.get("task")
    experiment_type = res.get("experiment_type", "monolingual")
    submetric = res.get("submetric")
    layer = res.get("layer", extract_layer(model_key))
    is_control = res.get("is_control", False)
    control_index = res.get("control_index")
    source = res.get("source", "baseline" if "tfidf" in model_key or "xgboost" in model_key  or "dummy" in model_key else "glot500")

    if "language" in res: 
        lang = res["language"]
        for split in ["val", "test"]:
            split_metrics = res.get(f"{split}_metrics", {})
            for metric, value in split_metrics.items():
                if value is None:
                    continue
                row = {
                    "model_key": model_key,
                    "task": task,
                    "model_type": model_type,
                    "experiment_type": experiment_type,
                    "submetric": submetric,
                    "source": source,
                    "layer": layer,
                    "split": split,
                    "language": lang,
                    "metric": metric,
                    "value": value,
                    "is_control": is_control,
                    "control_index": control_index,
                }
                rows.append(row)
                if is_control:
                    control_accumulator[(task, submetric, lang, split, metric)].append(value)
    else: 
        per_lang = res.get("per_language_metrics", {})
        for split in ["val", "test"]:
            lang_metrics = per_lang.get(split, {})
            for lang, metrics in lang_metrics.items():
                for metric, value in metrics.items():
                    if value is None:
                        continue
                    row = {
                        "model_key": model_key,
                        "task": task,
                        "model_type": model_type,
                        "experiment_type": experiment_type,
                        "submetric": submetric,
                        "source": source,
                        "layer": layer,
                        "split": split,
                        "language": lang,
                        "metric": metric,
                        "value": value,
                        "is_control": is_control,
                        "control_index": control_index,
                    }
                    rows.append(row)
                    if is_control:
                        control_accumulator[(task, submetric, lang, split, metric)].append(value)

df = pd.DataFrame(rows)

def display_scrollable_df(df, rows=10000, width=1200, height=400):
    html = df.head(rows).to_html()
    display(HTML(f"""
    <div style="width:{width}px; height:{height}px; overflow:auto; border:1px solid lightgray">
        {html}
    </div>
    """))

print("parsed rows:", len(df))
print("unique model keys:", df['model_key'].nunique())
print("tasks found:", df['task'].unique())
print("sources:", df['source'].unique())
print("example rows:")

display_scrollable_df(df)

df.to_csv('/home/robin/Research/qtype-eval/scripts/visualization/combined_results/analysis_output/result_table.csv', index=False, encoding='utf-8', sep=',', header=True)


parsed rows: 11172
unique model keys: 1051
tasks found: ['complexity' 'question_type' 'single_submetric']
sources: ['baseline' 'tfidf' 'glot500']
example rows:
